In [1]:
import random
from IPython.core.display import SVG
import pyomo.environ as pyo
from pysat.solvers import Solver
from pysat.formula import CNF 
import py_svg_combinatorics as psc
from ipywidgets import widgets, HBox
from collections import Counter
from pprint import pprint
from random import randint
import numpy as np
from IPython.display import IFrame
import IPython
from copy import copy
import os
from pathlib import Path
np.set_printoptions(precision=2)
np.set_printoptions(suppress=True)
nbname = ''
try:
    nbname = __vsc_ipynb_file__
except:
    if 'COCALC_JUPYTER_FILENAME' in os.environ:
        nbname = os.environ['COCALC_JUPYTER_FILENAME']    
title_ = Path(nbname).stem.replace('-', '_').title()    
IFrame(f'https://discopal.ispras.ru/index.php?title=Hardprob/{title_}&useskin=cleanmonobook', width=1280, height=300)

In [2]:
# Случайные данные
m = np.random.randint(3, 20)
n = np.random.randint(3, 20)
A = np.random.randint(1, 100, size=(m,n))
c = np.random.randint(2, size=(n))
b = np.floor(1/np.random.rand(m))

# Увеличиваем вероятность нетривиального решения
for i in range(len(b)):
    b[i] = max(b[i], max(A[i, j] for j in range(n)))


A, b, c


(array([[38,  3, 56, 83, 95],
        [95, 58, 46, 40, 46],
        [14, 91, 61, 71, 72],
        [96,  1, 37,  9, 41],
        [30, 73, 32, 33, 73],
        [28, 77, 57, 56, 94],
        [ 8, 96, 62, 31, 61],
        [48, 91, 54, 29, 92],
        [64, 54, 51, 68, 37],
        [39, 67, 39, 30, 85]]),
 array([95., 95., 91., 96., 73., 94., 96., 92., 68., 85.]),
 array([1, 0, 0, 0, 1]))

In [3]:
def get_model(A, b, c):
    m = pyo.ConcreteModel()

    m.m, m.n = A.shape

    # на всякий случай, возьмем с собой
    m.A = A
    m.b = b
    m.c = c
    
    m.I = range(m.m)
    m.J = range(m.n)
    
    m.x = pyo.Var(m.J, domain=pyo.Binary)
    m.obj = pyo.Objective(expr = sum( c[j] * m.x[j] for j in m.J), sense=pyo.maximize)

    @m.Constraint(m.I)
    def строчка_не_больше(m, i):
        return sum(A[i, j] * m.x[j] for j in m.J) <= b[i]

    return m

m = get_model(A, b, c)
m.pprint()

2 Set Declarations
    x_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :    5 : {0, 1, 2, 3, 4}
    строчка_не_больше_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   10 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9}

1 Var Declarations
    x : Size=5, Index=x_index
        Key : Lower : Value : Upper : Fixed : Stale : Domain
          0 :     0 :  None :     1 : False :  True : Binary
          1 :     0 :  None :     1 : False :  True : Binary
          2 :     0 :  None :     1 : False :  True : Binary
          3 :     0 :  None :     1 : False :  True : Binary
          4 :     0 :  None :     1 : False :  True : Binary

1 Objective Declarations
    obj : Size=1, Index=None, Active=True
        Key  : Active : Sense    : Expression
        None :   True : maximize : x[0] + 0*x[1] + 0*x[2] + 0*x[3] + x[4]

1 Constraint Declarations
    строчка

In [4]:
def print_solution(m):
    for v in m.component_data_objects(pyo.Var):
        if v.value and v.value > 0:
            print(str(v), v.value)

In [5]:
solver = pyo.SolverFactory('cbc')
solver.solve(m).write()
print_solution(m)

# ==========================================================
# = Solver Results                                         =
# ==========================================================
# ----------------------------------------------------------
#   Problem Information
# ----------------------------------------------------------
Problem: 
- Name: unknown
  Lower bound: 1.0
  Upper bound: 1.0
  Number of objectives: 1
  Number of constraints: 8
  Number of variables: 2
  Number of binary variables: 5
  Number of integer variables: 5
  Number of nonzeros: 2
  Sense: maximize
# ----------------------------------------------------------
#   Solver Information
# ----------------------------------------------------------
Solver: 
- Status: ok
  User time: -1.0
  System time: 0.0
  Wallclock time: 0.01
  Termination condition: optimal
  Termination message: Model was solved to optimality (subject to tolerances), and an optimal solution is available.
  Statistics: 
    Branch and bound: 
      N